### Sofía Álvarez, Brenda Barahona, Álvaro Plata
<h1 align='center'> Laboratorio 5</h1>

WWI (World Wide Importers) 1 es una empresa encargada de realizar importaciones y venderlas a diferentes clientes en diferentes ciudades de Estados Unidos. Actualmente, la empresa se encuentra buscando servicios de consultoría de BI puesto que desean optimizar sus ganancias, pues consideran que algunos de sus productos no están generando las ganancias que deberían. También, están interesados en saber si hay otros factores que le impiden optimizar sus ganancias. Dado lo anterior, WWI lo contrata a usted para que realice una consultoría de BI, en particular en esta fase, para la creación de la base de datos, la carga de datos y unas consultas iniciales que permitan validar el proceso previo. En esta ocasión quiere que el trabajo lo realicen en grupos de máximo 3 estudiantes, con el fin de comparar dos herramientas que está evaluando para utilizar a futuro en procesos de ETL.
Para esta etapa de la consultoría, la empresa requiere que usted implemente un proceso ETL que le permita extraer los datos de órdenes desde unos archivos CSV y almacenarlos en un modelo dimensional tal que les permita realizar análisis para mejorar entre otros elementos, su eficiencia operativa.

## Análisis exploratorio de los datos y preprocesamiento

In [1]:
#Instalamos las dependencias necesarias
#!pip3 install pandas_profiling
#!pip3 install pandas==1.2

Se realizará el análisis exploratorio para cada uno de los datasets proveídos por WWI

In [2]:
# Se importan las librerías y dependencias necesarias para la ejecución del notebook
import numpy as np
import pandas as pd
import matplotlib as plt
from pandas_profiling import ProfileReport

### Variable Dimension City

In [3]:
datos_dim_city = pd.read_csv('datos_originales/dimension_city.csv', delimiter=',')
datos_dim_city.sample(5)

row ID  City_Key               City State_Province        Country  \
55  Row55        55            El Nido     California  United States   
87  Row87        87               Elba       New York  United States   
64  Row64        64          El Portal        Florida  United States   
7    Row7         7         Carrollton        Georgia  United States   
62  Row62        62  El Paso de Robles     California  United States   

        Continent Sales_Territory    Region         Subregion  \
55  North America        Far West  Americas  Northern America   
87  North America         Mideast  Americas  Northern America   
64  North America       Southeast  Americas  Northern America   
7   North America       Southeast  Americas  Northern America   
62  North America        Far West  Americas  Northern America   

    Latest_Recorded_Population  
55                         330  
87                         676  
64                        2325  
7                        24388  
62                       29793

Observamos las primeras filas del dataset

In [4]:
datos_dim_city.head()

row ID  City_Key        City State_Province        Country      Continent  \
0   Row0         0     Unknown            NaN            NaN            NaN   
1   Row1         1  Carrollton       New York  United States  North America   
2   Row2         2  Carrollton       Virginia  United States  North America   
3   Row3         3  Carrollton       Illinois  United States  North America   
4   Row4         4  Carrollton       Missouri  United States  North America   

  Sales_Territory    Region         Subregion  Latest_Recorded_Population  
0             NaN       NaN               NaN                           0  
1         Mideast  Americas  Northern America                           0  
2       Southeast  Americas  Northern America                        4574  
3     Great Lakes  Americas  Northern America                        2484  
4          Plains  Americas  Northern America                        3784

Vemos que la primera fila, con row ID Row0, no aporta información relevante pues todos sus datos están ausentes. Procedemos entonces a eliminarla.

In [5]:
datos_dim_city = datos_dim_city.drop(0)
#Verificamos que se eliminó correctamente
datos_dim_city.head()

row ID  City_Key        City State_Province        Country      Continent  \
1   Row1         1  Carrollton       New York  United States  North America   
2   Row2         2  Carrollton       Virginia  United States  North America   
3   Row3         3  Carrollton       Illinois  United States  North America   
4   Row4         4  Carrollton       Missouri  United States  North America   
5   Row5         5  Carrollton           Ohio  United States  North America   

  Sales_Territory    Region         Subregion  Latest_Recorded_Population  
1         Mideast  Americas  Northern America                           0  
2       Southeast  Americas  Northern America                        4574  
3     Great Lakes  Americas  Northern America                        2484  
4          Plains  Americas  Northern America                        3784  
5     Great Lakes  Americas  Northern America                        3241

Veamos, ahora, el número de filas y columnas que tenemos en nuestro conjunto de datos:

In [6]:
print("Número de filas o datos: {}".format(len(datos_dim_city)))
print("Número de columnas o variables: {}".format(len(datos_dim_city.columns)))

Número de filas o datos: 97
Número de columnas o variables: 10


Vemos que tenemos 98 datos (filas) y 10 columnas (variables).

Para ver una exploración más exhaustiva, hicimos un pandas profiling de los datos que nos fueron entregados:

In [7]:
profiling = ProfileReport(datos_dim_city)
profiling.to_file(output_file="pandas_profiling/dimension_city_pandas_profiling.html")
profiling

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

Export report to file:   0%|          | 0/1 [00:00<?, ?it/s]

Del anterior reporte podemos concluir y considerar:

- No encontamos filas duplicadas
- Las variables row ID y City_Key tienen un valor distinto en cada fila. 
- No encontramos celdas ausentes.
- Las variables Country, Continent, Region y Subregion tienen el mismo valor en todas las celdas. 

Asimismo, revisamos que los tipos de datos coincidan con lo esperado por el comando de <code>CREATE TABLE</code>:
```SQL
CREATE TABLE IF NOT EXISTS city(
            City_Key INT PRIMARY KEY,
            City VARCHAR(150),
            State_Province VARCHAR(150),
            Country VARCHAR(150),
            Continent VARCHAR(150),
            Sales_Territory VARCHAR(150),
            Region VARCHAR(150),
            Subregion VARCHAR(150),
            Latest_Recorded_Population INT
        );

```

In [8]:
datos_dim_city.dtypes

row ID                        object
City_Key                       int64
City                          object
State_Province                object
Country                       object
Continent                     object
Sales_Territory               object
Region                        object
Subregion                     object
Latest_Recorded_Population     int64
dtype: object

Como vemos, todos los tipos de datos coinciden con lo que esperan las columnas. Veamos si hay algún dato que exceda el tamaño:

In [9]:
oor = len(datos_dim_city[datos_dim_city['City'].str.len() > 150]) + \
len(datos_dim_city[datos_dim_city['State_Province'].str.len() > 150]) + \
len(datos_dim_city[datos_dim_city['Country'].str.len() > 150]) + \
len(datos_dim_city[datos_dim_city['Continent'].str.len() > 150]) + \
len(datos_dim_city[datos_dim_city['Sales_Territory'].str.len() > 150]) + \
len(datos_dim_city[datos_dim_city['Region'].str.len() > 150]) + \
len(datos_dim_city[datos_dim_city['Subregion'].str.len() > 150])
print('La cantidad de datos que exceden el tamaño es: ', oor)

La cantidad de datos que exceden el tamaño es:  0


Es importante notar que la columna row ID no es esperada por las tablas entonces debe eliminarse.

### Variable Dimension Customer
Es importante anotar que ignoramos los errores de decodificación tipo utf-8 para evitar problemas en la lectura y análisis:

In [10]:
datos_dim_cust = pd.read_csv('datos_originales/dimension_customer.csv', delimiter=',', 
                             encoding='utf-8', encoding_errors='ignore')
datos_dim_cust.head()

Customer_Key                            Customer  \
0             0                             Unknown   
1             1         Tailspin Toys (Head Office)   
2             2       Tailspin Toys (Sylvanite- MT)   
3             3  Tailspin Toys (Peeples Valley- AZ)   
4             4  Tailspin Toys (Medicine Lodge- KS)   

              Bill_To_Customer      Category   Buying_Group  \
0                          NaN           NaN            NaN   
1  Tailspin Toys (Head Office)  Novelty Shop  Tailspin Toys   
2  Tailspin Toys (Head Office)  Novelty Shop  Tailspin Toys   
3  Tailspin Toys (Head Office)  Novelty Shop  Tailspin Toys   
4  Tailspin Toys (Head Office)  Novelty Shop  Tailspin Toys   

      Primary_Contact  Postal_Code  
0                 NaN          NaN  
1      Waldemar Fisar      90410.0  
2      Lorena Cindric      90216.0  
3  Bhaargav Rambhatla      90205.0  
4        Daniel Roman      90152.0

Vemos que la primera fila, con Customer_Key 0, no aporta información relevante pues todos sus datos están ausentes. Procedemos entonces a eliminarla.

In [11]:
datos_dim_cust = datos_dim_cust.drop(0)
#Verificamos que se eliminó correctamente
datos_dim_cust.head()

Customer_Key                            Customer  \
1             1         Tailspin Toys (Head Office)   
2             2       Tailspin Toys (Sylvanite- MT)   
3             3  Tailspin Toys (Peeples Valley- AZ)   
4             4  Tailspin Toys (Medicine Lodge- KS)   
5             5         Tailspin Toys (Gasport- NY)   

              Bill_To_Customer      Category   Buying_Group  \
1  Tailspin Toys (Head Office)  Novelty Shop  Tailspin Toys   
2  Tailspin Toys (Head Office)  Novelty Shop  Tailspin Toys   
3  Tailspin Toys (Head Office)  Novelty Shop  Tailspin Toys   
4  Tailspin Toys (Head Office)  Novelty Shop  Tailspin Toys   
5  Tailspin Toys (Head Office)  Novelty Shop  Tailspin Toys   

      Primary_Contact  Postal_Code  
1      Waldemar Fisar      90410.0  
2      Lorena Cindric      90216.0  
3  Bhaargav Rambhatla      90205.0  
4        Daniel Roman      90152.0  
5     Johanna Huiting      90261.0

Veamos, ahora, el número de filas y columnas que tenemos en nuestro conjunto de datos:

In [12]:
print("Número de filas o datos: {}".format(len(datos_dim_cust)))

print("Número de columnas o variables: {}".format(len(datos_dim_cust.columns)))

Número de filas o datos: 402
Número de columnas o variables: 7


Para ver una exploración más exhaustiva, hicimos un pandas profiling de los datos que nos fueron entregados:

In [13]:
profiling = ProfileReport(datos_dim_cust)
profiling.to_file(output_file="pandas_profiling/dimension_customer_pandas_profiling.html")
profiling

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

Export report to file:   0%|          | 0/1 [00:00<?, ?it/s]

Del anterior reporte podemos concluir y considerar:
- No encontamos filas duplicadas
- No encontramos celdas ausentes.
- La Variable Category tiene un único valor. 
- Las variables Bill_To_Customer y Buying_Group aportan información similar.

Comparemos los tipos de datos con lo esperado por la tabla:
```SQL
    CREATE TABLE IF NOT EXISTS customer(
            Customer_Key INT PRIMARY KEY,
            Customer VARCHAR(150),
            Bill_To_Customer VARCHAR(150),
            Category VARCHAR(150),
            Buying_Group VARCHAR(150),
            Primary_Contact VARCHAR(150),
            Postal_Code INT
        );
```

In [14]:
datos_dim_cust.dtypes

Customer_Key          int64
Customer             object
Bill_To_Customer     object
Category             object
Buying_Group         object
Primary_Contact      object
Postal_Code         float64
dtype: object

Vemos que el código postal debe ser un int, entonces tenemos en cuenta esto para la transformación. Revisamos que no se exceda el tamaño:

In [15]:
oor = len(datos_dim_cust[datos_dim_cust['Customer'].str.len() > 150]) +\
len(datos_dim_cust[datos_dim_cust['Bill_To_Customer'].str.len() > 150]) +\
len(datos_dim_cust[datos_dim_cust['Category'].str.len() > 150]) +\
len(datos_dim_cust[datos_dim_cust['Buying_Group'].str.len() > 150]) +\
len(datos_dim_cust[datos_dim_cust['Primary_Contact'].str.len() > 150])
print('La cantidad de datos fuera de rango:', oor)

La cantidad de datos fuera de rango: 0


### Variable Dimension Date

In [16]:
datos_dim_date = pd.read_csv('datos_originales/dimension_date.csv', delimiter=',', encoding='utf-8', 
                             encoding_errors='ignore')
datos_dim_date.head()

Date_key  Day_Number  Day_val Month_val Short_Month  \
0  2013-01-01           1        1   January         Jan   
1  2013-01-02           2        2   January         Jan   
2  2013-01-03           3        3   January         Jan   
3  2013-01-04           4        4   January         Jan   
4  2013-01-05           5        5   January         Jan   

   Calendar_Month_Number  Calendar_Year  Fiscal_Month_Number  Fiscal_Year  
0                      1           2013                    3         2013  
1                      1           2013                    3         2013  
2                      1           2013                    3         2013  
3                      1           2013                    3         2013  
4                      1           2013                    3         2013

Veamos el número de filas y columnas que se encuentran en nuestro dataset. Notamos que corresponde exactamente a la cantidad de días en 4 años (incluyendo el año bisiesto - 2016 -).

In [17]:
print("Número de filas o datos: {}".format(len(datos_dim_date)))

print("Número de columnas o variables: {}".format(len(datos_dim_date.columns)))

Número de filas o datos: 1461
Número de columnas o variables: 9


Para ver una exploración más exhaustiva, hicimos un pandas profiling de los datos que nos fueron entregados:

In [18]:
profiling = ProfileReport(datos_dim_date, minimal=True)
profiling.to_file(output_file="pandas_profiling/dimension_date_pandas_profiling.html")
profiling

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

Export report to file:   0%|          | 0/1 [00:00<?, ?it/s]

Del anterior reporte podemos concluir y considerar:
- No encontamos filas duplicadas
- No encontramos celdas ausentes.
- Las variables Day_Number y Day_val aportan la misma información, por lo que podemos considerar eliminar una de las 2.
- Las variables Month_val y Short_Month aportan la misma información, por lo que podemos considerar eliminar una de las 2.
Comparemos con lo que la tabla está esperando:
```SQL
CREATE TABLE IF NOT EXISTS date_table(
            Date_key DATE PRIMARY KEY,
            Day_Number INT,
            Day_val INT,
            Month_val VARCHAR(20),
            Short_Month VARCHAR(10),
            Calendar_Month_Number INT,
            Calendar_Year INT,
            Fiscal_Month_Number INT,
            Fiscal_Year INT
        );
```

In [19]:
datos_dim_date.dtypes

Date_key                 object
Day_Number                int64
Day_val                   int64
Month_val                object
Short_Month              object
Calendar_Month_Number     int64
Calendar_Year             int64
Fiscal_Month_Number       int64
Fiscal_Year               int64
dtype: object

La única que discrepa es <code>Date_key</code>. No obstante, no es un problema sustancial puesto que esto se corrige en la lectura, usando la función <code>TO_DATE</code> en el SAL. Veamos si algún dato excede el límite:

In [20]:
oor = len(datos_dim_date[datos_dim_date['Month_val'].str.len() > 20]) +\
len(datos_dim_date[datos_dim_date['Short_Month'].str.len() > 10])
print('Cantidad de datos fuera de rango:', oor)

Cantidad de datos fuera de rango: 0


### Variable Dimension Employee

In [21]:
datos_dim_emp = pd.read_csv('datos_originales/dimension_employee.csv', delimiter=',', encoding='utf-8')
datos_dim_emp.head()

Employee_Key       Employee Preferred_Name  Is_Salesperson
0             0        Unknown            NaN           False
1             1      Lily Code           Lily            True
2             2  Isabella Rupp       Isabella           False
3             3   Ethan Onslow          Ethan           False
4             4      Amy Trefl            Amy            True

Vemos que la primera fila, con Employee_Key 0, no aporta información relevante pues todos sus datos están ausentes. Procedemos entonces a eliminarla.

In [22]:
datos_dim_emp = datos_dim_emp.drop(0)
#Verificamos que se eliminó correctamente
datos_dim_emp.head()

Employee_Key       Employee Preferred_Name  Is_Salesperson
1             1      Lily Code           Lily            True
2             2  Isabella Rupp       Isabella           False
3             3   Ethan Onslow          Ethan           False
4             4      Amy Trefl            Amy            True
5             5      Jai Shand            Jai           False

Observamos la cantidad de filas y columnas que se encuentran en nuestro dataset

In [23]:
print("Número de filas o datos: {}".format(len(datos_dim_emp)))
print("Número de columnas o variables: {}".format(len(datos_dim_emp.columns)))

Número de filas o datos: 212
Número de columnas o variables: 4


Para hacer una exploración más exhasutiva, hicimos un pandas profiling de los datos

In [24]:
profiling = ProfileReport(datos_dim_emp)
profiling.to_file(output_file="pandas_profiling/dimension_employee_pandas_profiling.html")
profiling

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

Export report to file:   0%|          | 0/1 [00:00<?, ?it/s]

Del anterior reporte podemos concluir y considerar:
- No encontamos filas duplicadas
- No encontramos celdas ausentes.

El único preprocesamiento que debe realizarse es que, para realizar la carga adecuada de los datos, cambiaremos los valores de True y False a '1' y '0'. Revisamos los tipos de datos esperados por la tabla y comparamos:

```SQL
CREATE TABLE IF NOT EXISTS employee(
            Employee_Key INT PRIMARY KEY,
            Employee VARCHAR(150),
            Preferred_Name VARCHAR(150),
            Is_Salesperson BOOLEAN
        );
```

In [25]:
datos_dim_emp.dtypes

Employee_Key       int64
Employee          object
Preferred_Name    object
Is_Salesperson      bool
dtype: object

Vemos que los tipos de datos coinciden. No obstante, hacemos la conversión del booleano aceptado en Python por el de las tablas. Elegimos, en este caso, '1' y '0' para true y false, respectivamente. Asimismo, chequeamos que la longitud de todos los campos de string sea menor a 150:

In [26]:
out_of_range = len(datos_dim_emp[datos_dim_emp['Employee'].str.len() > 150]) +\
len(datos_dim_emp[datos_dim_emp['Preferred_Name'].str.len() > 150])
print('La cantidad de datos que exceden la longitud es:', out_of_range)

La cantidad de datos que exceden la longitud es: 0


### Variable Dimension Stock Item

In [27]:
datos_dim_stock = pd.read_csv('datos_originales/dimension_stock_item.csv', delimiter=',', 
                              encoding='utf-8', encoding_errors='ignore')
datos_dim_stock.head()

Stock_Item_Key                        Stock_Item Color Selling_Package  \
0               0                           Unknown   NaN             NaN   
1               1  Void fill 400 L bag (White) 400L   NaN            Each   
2               2  Void fill 300 L bag (White) 300L   NaN            Each   
3               3  Void fill 200 L bag (White) 200L   NaN            Each   
4               4  Void fill 100 L bag (White) 100L   NaN            Each   

  Buying_Package Brand Size_val  Lead_Time_Days  Quantity_Per_Outer  \
0            NaN   NaN      NaN               0                   0   
1           Each   NaN     400L              14                  10   
2           Each   NaN     300L              14                  10   
3           Each   NaN     200L              14                  10   
4           Each   NaN     100L              14                  10   

   Is_Chiller_Stock Tax_Rate Unit_Price Recommended_Retail_Price  \
0             False     ,000        ,00                      ,00   
1             False   14,000      50,00                    74,75   
2             False   14,000      37,50                    56,06   
3             False   14,000      25,00                    37,38   
4             False   14,000      12,50                    18,69   

  Typical_Weight_Per_Unit  
0                    ,000  
1                   1,000  
2                    ,750  
3                    ,500  
4                    ,250

Vemos que la primera fila, con Item_Key 0, no aporta información relevante pues todos sus datos están ausentes. Procedemos entonces a eliminarla.

In [28]:
datos_dim_stock = datos_dim_stock.drop(0)
#Verificamos que se eliminó correctamente
datos_dim_stock.head()

Stock_Item_Key                        Stock_Item Color Selling_Package  \
1               1  Void fill 400 L bag (White) 400L   NaN            Each   
2               2  Void fill 300 L bag (White) 300L   NaN            Each   
3               3  Void fill 200 L bag (White) 200L   NaN            Each   
4               4  Void fill 100 L bag (White) 100L   NaN            Each   
5               5        Air cushion machine (Blue)   NaN            Each   

  Buying_Package Brand Size_val  Lead_Time_Days  Quantity_Per_Outer  \
1           Each   NaN     400L              14                  10   
2           Each   NaN     300L              14                  10   
3           Each   NaN     200L              14                  10   
4           Each   NaN     100L              14                  10   
5           Each   NaN      NaN              20                   1   

   Is_Chiller_Stock Tax_Rate Unit_Price Recommended_Retail_Price  \
1             False   14,000      50,00                    74,75   
2             False   14,000      37,50                    56,06   
3             False   14,000      25,00                    37,38   
4             False   14,000      12,50                    18,69   
5             False   20,000    1899,00                  2839,01   

  Typical_Weight_Per_Unit  
1                   1,000  
2                    ,750  
3                    ,500  
4                    ,250  
5                  10,000

Observamos la cantidad de filas y columnas presentes en el dataset

In [29]:
print("Número de filas o datos: {}".format(len(datos_dim_stock)))
print("Número de columnas o variables: {}".format(len(datos_dim_stock.columns)))

Número de filas o datos: 671
Número de columnas o variables: 14


Para hacer una exploración más exhaustiva, hicimos un pandas profiling de los datos

In [30]:
profiling = ProfileReport(datos_dim_stock)
profiling.to_file(output_file="pandas_profiling/dimension_stock_item_pandas_profiling.html")
profiling

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

Export report to file:   0%|          | 0/1 [00:00<?, ?it/s]

Del anterior reporte podemos concluir y considerar:
- No encontamos filas duplicadas
- Encontramos 1118 celdas vacías que corresponden al 11.1% de los datos, estos datos se completarán con la función de fillNa de python.
- Observamos que la variable Brand tiene un valor constante en las celdas que tienen un valor asignado, pero además presenta un 90% de ausencias.
- Cambiaremos los valores booleanos por su respectivo valor en string, '1' o '0'.

Revisamos además los tipos de datos esperados por la tabla:
```SQL
CREATE TABLE IF NOT EXISTS stockitem(
            Stock_Item_Key INT PRIMARY KEY,
            WWI_Stock_Item_ID INT,
            Stock_Item VARCHAR(200),
            Color VARCHAR(50),
            Selling_Package VARCHAR(50),
            Buying_Package VARCHAR(50),
            Brand VARCHAR(50),
            Size_val VARCHAR(50),
            Lead_Time_Days INT,
            Quantity_Per_Outer INT,
            Is_Chiller_Stock BOOLEAN,
            Tax_Rate DECIMAL,
            Unit_Price DECIMAL,
            Recommended_Retail_Price DECIMAL,
            Typical_Weight_Per_Unit DECIMAL
        );
```

In [31]:
datos_dim_stock.dtypes

Stock_Item_Key               int64
Stock_Item                  object
Color                       object
Selling_Package             object
Buying_Package              object
Brand                       object
Size_val                    object
Lead_Time_Days               int64
Quantity_Per_Outer           int64
Is_Chiller_Stock              bool
Tax_Rate                    object
Unit_Price                  object
Recommended_Retail_Price    object
Typical_Weight_Per_Unit     object
dtype: object

Primero, notamos que no hay ninguna columna denominada WWI_Stock_Item_ID, por lo que debe eliminarse esta de la creación de tablas. Segundo, los últimos 4 tipos de datos son leídos como strings y realmente son decimales. Esto también debe ser modificado en python. Miramos además si algún dato excede la longitud máxima:

In [32]:
oor = len(datos_dim_stock[datos_dim_stock['Stock_Item'].str.len() > 200]) +\
len(datos_dim_stock[datos_dim_stock['Color'].str.len() > 50]) +\
len(datos_dim_stock[datos_dim_stock['Selling_Package'].str.len() > 50]) +\
len(datos_dim_stock[datos_dim_stock['Buying_Package'].str.len() > 50]) +\
len(datos_dim_stock[datos_dim_stock['Brand'].str.len() > 50]) +\
len(datos_dim_stock[datos_dim_stock['Size_val'].str.len() > 50]) 
print('La cantidad de datos fuera de rango es: ', oor)

La cantidad de datos fuera de rango es:  0


## Preprocesamiento de los datos

### Variable Dimension City
Eliminamos la columna row ID.

In [33]:
datos_dim_city = datos_dim_city.drop(['row ID'], axis=1)

In [34]:
datos_dim_city.head()

City_Key        City State_Province        Country      Continent  \
1         1  Carrollton       New York  United States  North America   
2         2  Carrollton       Virginia  United States  North America   
3         3  Carrollton       Illinois  United States  North America   
4         4  Carrollton       Missouri  United States  North America   
5         5  Carrollton           Ohio  United States  North America   

  Sales_Territory    Region         Subregion  Latest_Recorded_Population  
1         Mideast  Americas  Northern America                           0  
2       Southeast  Americas  Northern America                        4574  
3     Great Lakes  Americas  Northern America                        2484  
4          Plains  Americas  Northern America                        3784  
5     Great Lakes  Americas  Northern America                        3241

Guardamos los datos procesados de esta variable en un archivo csv para ser usado posteriormente

In [35]:
datos_dim_city.to_csv("datos_procesados/dimension_city.csv")

### Variable Dimension Customer
Convertimos el código postal en un número entero

In [36]:
datos_dim_cust['Postal_Code'] = datos_dim_cust['Postal_Code'].astype(int)

In [37]:
datos_dim_cust.head()

Customer_Key                            Customer  \
1             1         Tailspin Toys (Head Office)   
2             2       Tailspin Toys (Sylvanite- MT)   
3             3  Tailspin Toys (Peeples Valley- AZ)   
4             4  Tailspin Toys (Medicine Lodge- KS)   
5             5         Tailspin Toys (Gasport- NY)   

              Bill_To_Customer      Category   Buying_Group  \
1  Tailspin Toys (Head Office)  Novelty Shop  Tailspin Toys   
2  Tailspin Toys (Head Office)  Novelty Shop  Tailspin Toys   
3  Tailspin Toys (Head Office)  Novelty Shop  Tailspin Toys   
4  Tailspin Toys (Head Office)  Novelty Shop  Tailspin Toys   
5  Tailspin Toys (Head Office)  Novelty Shop  Tailspin Toys   

      Primary_Contact  Postal_Code  
1      Waldemar Fisar        90410  
2      Lorena Cindric        90216  
3  Bhaargav Rambhatla        90205  
4        Daniel Roman        90152  
5     Johanna Huiting        90261

Ahora todos los tipos de datos coinciden con lo esperado por las tablas. Guardamos los datos procesados de esta variable en un archivo csv para ser usado posteriormente

Revisamos si hay datos con comillas. Los eliminamos para no tener errores en la carga de datos:

In [38]:
datos_dim_cust['Bill_To_Customer'] = datos_dim_cust['Bill_To_Customer'].str.replace("'", "")
datos_dim_cust['Category'] = datos_dim_cust['Category'].str.replace("'", "")
datos_dim_cust['Buying_Group'] = datos_dim_cust['Buying_Group'].str.replace("'", "")
datos_dim_cust['Customer'] = datos_dim_cust['Customer'].str.replace("'", "")

In [39]:
datos_dim_cust.to_csv("datos_procesados/dimension_customer.csv")

### Variable Dimension Date

In [40]:
datos_dim_date.head()

Date_key  Day_Number  Day_val Month_val Short_Month  \
0  2013-01-01           1        1   January         Jan   
1  2013-01-02           2        2   January         Jan   
2  2013-01-03           3        3   January         Jan   
3  2013-01-04           4        4   January         Jan   
4  2013-01-05           5        5   January         Jan   

   Calendar_Month_Number  Calendar_Year  Fiscal_Month_Number  Fiscal_Year  
0                      1           2013                    3         2013  
1                      1           2013                    3         2013  
2                      1           2013                    3         2013  
3                      1           2013                    3         2013  
4                      1           2013                    3         2013

Guardamos los datos procesados de esta variable en un archivo csv para ser usado posteriormente

In [41]:
datos_dim_date.to_csv("datos_procesados/dimension_date.csv")

### Variable dimensión Employee

Hacemos el preprocesamiento correspondiente a la variable Employee, para cambiar los booleanos a enteros:

In [54]:
datos_dim_emp['Is_Salesperson'] = datos_dim_emp['Is_Salesperson'].astype(int) 
datos_dim_emp['Is_Salesperson'] = datos_dim_emp['Is_Salesperson'].astype(str) 

Revisamos que hayan quedado adecuadamente modificados:

In [55]:
datos_dim_emp.sample(5)

Employee_Key        Employee Preferred_Name Is_Salesperson
107           107       Taj Shand            Taj              1
18             18     Eva Muirden            Eva              0
158           158  Anthony Grosse        Anthony              1
15             15  Kayla Woodcock          Kayla              1
209           209      Piper Koch          Piper              0

Procedemos a guardar el csv de Employee:

In [44]:
datos_dim_emp.to_csv("datos_procesados/dimension_employee.csv")

### Variable Dimension Stock Item

In [45]:
# Cambiando los valores booleanos
datos_dim_stock['Is_Chiller_Stock'] = datos_dim_stock['Is_Chiller_Stock'].astype(int) 
datos_dim_stock['Is_Chiller_Stock'] = datos_dim_stock['Is_Chiller_Stock'].astype(str)
# Llenando los valores nulos
datos_dim_stock.fillna('NA', inplace=True)
# Cambiando los datos de string a numerico
datos_dim_stock[['Tax_Rate', 'Unit_Price', 'Recommended_Retail_Price', 'Typical_Weight_Per_Unit']] = datos_dim_stock[['Tax_Rate', 'Unit_Price', 'Recommended_Retail_Price', 'Typical_Weight_Per_Unit']].replace(',', '.', regex=True)
datos_dim_stock[['Tax_Rate', 'Unit_Price', 'Recommended_Retail_Price', 'Typical_Weight_Per_Unit']] = datos_dim_stock[['Tax_Rate', 'Unit_Price', 'Recommended_Retail_Price', 'Typical_Weight_Per_Unit']].astype(float)

Revisemos que las transformaciones hayan sido exitosas:

In [46]:
datos_dim_stock.sample(5)

Stock_Item_Key                                         Stock_Item  Color  \
57               57                 32 mm Double sided bubble wrap 20m     NA   
146             146  Ride on vintage American toy coupe (Black) 1/1...  Black   
595             595  USB food flash drive - dim sum 10 drive variet...     NA   
448             448                            Chocolate echidnas 250g     NA   
455             455  RC big wheel monster truck with remote control...  Black   

    Selling_Package Buying_Package      Brand    Size_val  Lead_Time_Days  \
57             Each           Each         NA         20m              14   
146            Each           Each  Northwind  1/12 scale              14   
595          Packet         Packet         NA          NA              14   
448             Bag         Carton         NA        250g               3   
455            Each           Each  Northwind  1/50 scale              14   

     Quantity_Per_Outer Is_Chiller_Stock  Tax_Rate  Unit_Price  \
57                   10                0      14.0       37.00   
146                   1                0      14.0      285.00   
595                   1                0      14.0      240.00   
448                  24                1       3.0        8.55   
455                   1                0      14.0       45.00   

     Recommended_Retail_Price  Typical_Weight_Per_Unit  
57                      55.32                     6.00  
146                    426.08                    18.00  
595                    358.80                     0.50  
448                     12.23                     0.25  
455                     67.28                     1.80

Comprobamos que los tipos de datos ahora sean los adecuados:

In [47]:
datos_dim_stock.dtypes

Stock_Item_Key                int64
Stock_Item                   object
Color                        object
Selling_Package              object
Buying_Package               object
Brand                        object
Size_val                     object
Lead_Time_Days                int64
Quantity_Per_Outer            int64
Is_Chiller_Stock             object
Tax_Rate                    float64
Unit_Price                  float64
Recommended_Retail_Price    float64
Typical_Weight_Per_Unit     float64
dtype: object

Revisamos si hay datos con comillas. Los eliminamos para no tener errores en la carga de datos:

In [48]:
datos_dim_stock['Stock_Item'] = datos_dim_stock['Stock_Item'].str.replace("'", "")

Guardamos los datos procesados de esta variable en un archivo csv para ser usado posteriormente

In [49]:
datos_dim_stock.to_csv("datos_procesados/dimension_stock_item.csv")